# Solar Power Generated Prediction

In [27]:
# import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import warnings
warnings.simplefilter("ignore")

In [28]:
# lets read the dataset
dforig = pd.read_csv(r'./solar_data.csv')
#---------------------------------------------------------------------------------------------------------------------------------------------#
# Extract a 99% sample for training and validation (df). This subset represents a manageable portion of the entire dataset and helps reduce 
# computational costs during model development.
#---------------------------------------------------------------------------------------------------------------------------------------------#
df = dforig.sample(frac=0.99, random_state=77)
#---------------------------------------------------------------------------------------------------------------------------------------------#
# Extract the 1% of the rest data sample for model evaluation with unseen data (df_rest). This smaller subset contributes to assessing the 
# model's generalization performance.
#---------------------------------------------------------------------------------------------------------------------------------------------#
df_rest = dforig.drop(df.index)
#---------------------------------------------------------------------------------------------------------------------------------------------#
# To optimize memory usage, the original dataset (dforig) is deleted from memory after extracting the necessary subsets.
#---------------------------------------------------------------------------------------------------------------------------------------------#
del dforig
df.head(10)

Timestamp   Air_Temp  Relative_Humidity  Wind_Speed  \
162  27-04-2022 20:56  18.537628          33.688504    0.000000   
926  28-04-2022 22:24  18.375376          37.263612    0.000000   
658  28-04-2022 13:28  47.342700          15.605986    0.266667   
403  28-04-2022 04:58  13.176992          49.583320    0.000000   
863  28-04-2022 20:18  19.861064          33.851000    0.000000   
991  29-04-2022 00:34  17.223208          41.051480    0.000000   
38   27-04-2022 16:48  37.459356          12.291790    1.200000   
943  28-04-2022 22:58  17.976490          37.975288    0.000000   
100  27-04-2022 18:52  21.950574          28.242694    0.000000   
516  28-04-2022 08:44  24.343190          31.317602    0.000000   

     Wind_Direction  Solar_Radiation       RTD_1       RTD_2       RTD_3  \
162      204.482400        -0.192932   25.286246   26.652346   25.943926   
926      214.652560         0.109741   25.022490   26.429094   25.855010   
658      244.755260       979.989840  115.570260  110.079440  108.073940   
403      214.352420        -0.302673   19.982922   21.432504   20.929688   
863      190.918260        -0.171028   26.920608   28.403816   27.810462   
991       97.118104        -0.678139   23.828354   25.240518   24.689474   
38       207.594940       346.472040   93.590552   93.097720   89.474672   
943      182.017020        -0.328339   24.735550   26.143934   25.603566   
100      222.996580         4.756264   29.005122   30.494070   29.668420   
516       13.749242       183.381980   44.196000   41.963548   40.902112   

          RTD_4       RTD_5  Array_Voltage  Array_Current  Power_Generated  
162   25.888712   26.084400       2.669876       5.394390        14.402352  
926   25.703916   25.890412       2.633171       5.396225        14.209184  
658  110.888840  110.431460      69.743776       5.355900       373.540640  
403   20.832998   20.936020       2.753002       5.405689        14.881874  
863   27.525680   27.713874       1.745682       5.390672         9.410398  
991   24.613070   24.794178       2.775370       5.397441        14.979894  
38    92.165160   92.692704      78.852880       5.357844       422.481440  
943   25.453368   25.625432       2.674832       5.396430        14.434540  
100   29.418498   29.645642      51.416876       5.381770       276.713800  
516   48.058976   48.564848      56.677924       5.388231       305.393700

In [29]:
descriptions = [
    "The time at which the data was recorded",
    "The air temperature at the location",
    "Relative humidity of the air",
    "Wind speed at the location",
    "Direction from which the wind is blowing",
    "Amount of solar radiation received at the location",
    "Temperature values measured by Resistance Temperature Detector",
    "Temperature values measured by Resistance Temperature Detector",
    "Temperature values measured by Resistance Temperature Detector",
    "Temperature values measured by Resistance Temperature Detector",
    "Temperature values measured by Resistance Temperature Detector",
    "Voltage output from the photovoltaic array",
    "Current output from the photovoltaic array",
    "Power generated by the photovoltaic system",
]
for name_data, description in zip(df, descriptions):
    print(f"{name_data}: {description}")

Timestamp: The time at which the data was recorded
Air_Temp: The air temperature at the location
Relative_Humidity: Relative humidity of the air
Wind_Speed: Wind speed at the location
Wind_Direction: Direction from which the wind is blowing
Solar_Radiation: Amount of solar radiation received at the location
RTD_1: Temperature values measured by Resistance Temperature Detector
RTD_2: Temperature values measured by Resistance Temperature Detector
RTD_3: Temperature values measured by Resistance Temperature Detector
RTD_4: Temperature values measured by Resistance Temperature Detector
RTD_5: Temperature values measured by Resistance Temperature Detector
Array_Voltage: Voltage output from the photovoltaic array
Array_Current: Current output from the photovoltaic array
Power_Generated: Power generated by the photovoltaic system


In [30]:
print(f"Rows: {df.shape[0]}, Columns: {df.shape[1]}")

Rows: 999, Columns: 14


In [31]:
null_counts = df.isnull().sum()
null_percentages = (null_counts / len(df)) * 100
null_info = pd.DataFrame({'Null Count': null_counts, 'Null Percentage': null_percentages.map('{:.2f}%'.format), 'Dtype' : df.dtypes})
print(null_info)

                   Null Count Null Percentage    Dtype
Timestamp                   0           0.00%   object
Air_Temp                    0           0.00%  float64
Relative_Humidity           0           0.00%  float64
Wind_Speed                  0           0.00%  float64
Wind_Direction              0           0.00%  float64
Solar_Radiation             0           0.00%  float64
RTD_1                       0           0.00%  float64
RTD_2                       0           0.00%  float64
RTD_3                       0           0.00%  float64
RTD_4                       0           0.00%  float64
RTD_5                       0           0.00%  float64
Array_Voltage               0           0.00%  float64
Array_Current               0           0.00%  float64
Power_Generated             0           0.00%  float64


In [32]:
df.describe()

Air_Temp  Relative_Humidity  Wind_Speed  Wind_Direction  \
count  999.000000         999.000000  999.000000      999.000000   
mean    25.311078          31.825557    0.179246      210.572659   
std     11.397507          12.307919    0.434988       61.746491   
min     12.075478          10.648168    0.000000        1.577505   
25%     16.972601          20.061956    0.000000      194.260590   
50%     19.883582          34.883796    0.000000      212.511440   
75%     32.236961          42.153862    0.000000      230.116550   
max     49.631508          51.489112    2.933334      385.630880   

       Solar_Radiation       RTD_1       RTD_2       RTD_3       RTD_4  \
count       999.000000  999.000000  999.000000  999.000000  999.000000   
mean        222.123803   46.981014   46.777988   45.591897   46.500712   
std         355.905931   33.837982   31.490355   30.526311   31.808588   
min          -0.838326   19.737124   21.188662   20.738694   20.615538   
25%          -0.132198   23.860535   25.241221   24.739016   24.606665   
50%           1.433937   27.453532   28.789080   28.103806   27.971720   
75%         275.105730   65.922972   64.092754   64.913400   65.318558   
max        1132.128400  116.766760  111.630940  109.622220  111.680800   

            RTD_5  Array_Voltage  Array_Current  Power_Generated  
count  999.000000     999.000000     999.000000       999.000000  
mean    46.807646      34.022008       5.384039       182.707069  
std     31.932798      30.976352       0.018679       166.134275  
min     20.744964       1.574978       5.351294         8.485232  
25%     24.771727       2.657196       5.364579        14.353155  
50%     28.191964      51.296388       5.391468       275.995240  
75%     65.205970      63.116742       5.399351       338.932840  
max    111.628120      81.778936       5.407162       438.556840

# Visualizing the Data

In [33]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from scipy.stats import gaussian_kde

#---------------------------------------------------------------------------------------------------------------------------------------------#
# The grid of histograms with overlaid kernel density estimation (KDE) serves to unveil the underlying distribution and probability density of 
# each feature. This type of exploratory data analysis allows to assess the normality, skewness, and potential outliers within 
# each variable. Decision trees and KNN, being sensitive to the underlying data patterns, benefit significantly from a clear comprehension of 
# feature distributions. Thus, understanding the feature distributions is a critical step before feeding data into machine learning models.  
# These visualizations not only aid in preprocessing steps but also inform decisions on feature scaling, transformation, and outlier handling, 
# ultimately contributing to the robustness and accuracy of the machine learning models.
#---------------------------------------------------------------------------------------------------------------------------------------------#

fig1 = make_subplots(rows=3, cols=4, shared_yaxes=False, vertical_spacing=0.06)

fig1.update_layout(template="plotly_dark", font=dict(family="Montserrat"), width=1520, height=1140)

for i, col in enumerate(df.columns[1:13]):
    row_num = i // 4 + 1
    col_num = i % 4 + 1
    
    hist_trace = go.Histogram(x=df[col], nbinsx=32, histnorm='probability density', marker_color='#6331C5',
                              hovertemplate=f"<extra></extra><b>{col}</b><br><b>Bin:</b> %{{x}}<br><b>Prob. Density:</b> %{{y}}",)
    fig1.add_trace(hist_trace, row=row_num, col=col_num)
    
    # Kernel Density Estimation
    kernel = gaussian_kde(df[col])
    x_vals = np.linspace(df[col].min(), df[col].max(), 1000)
    y_vals = kernel(x_vals)
    
    kde_trace = go.Scatter(x=x_vals, y=y_vals, mode='lines', line=dict(color='#12BF80'), name='Kernel Density Estimation', hovertemplate="<extra></extra><b>Kernel Density Estimation</b>")
    fig1.add_trace(kde_trace, row=row_num, col=col_num)

    fig1.update_traces(
        marker=dict(line=dict(color="#F2F2F2", width=0.5)),
    )
    fig1.update_xaxes(title_text=col, row=row_num, col=col_num)
    if col_num == 1:
        fig1.update_yaxes(title_text="Probability Density", row=row_num, col=col_num)

fig1.update_layout(title='<b style="font-size:24px;">Distribution of Power Generated Features</b><br><span style="font-size:12px;">Probability Density</span>', showlegend=False)
fig1.show()


In [34]:
fig2 = go.Figure(data=[go.Histogram(
    x=df['Power_Generated'],
    nbinsx=32,
    histnorm='probability density',
    marker_color='#6331C5',
    hovertemplate=f"<extra></extra><b>{col}</b><br><b>Bin:</b> %{{x}}<br><b>Prob. Density:</b> %{{y}}",
)])

# Kernel Density Estimation
kernel = gaussian_kde(df['Power_Generated'])
x_vals = np.linspace(df['Power_Generated'].min(), df['Power_Generated'].max(), 1000)
y_vals = kernel(x_vals)
    
kde_trace = go.Scatter(x=x_vals, y=y_vals, mode='lines', line=dict(color='#12BF80'), name='Kernel Density Estimation', hovertemplate="<extra></extra><b>Kernel Density Estimation</b>")
fig2.add_trace(kde_trace)

fig2.update_traces(marker=dict(line=dict(color="#F2F2F2", width=0.5)))

fig2.update_layout(
    title='<b style="font-size:24px;">Distribution of Power Generated</b><br><span style="font-size:12px;">Probability Density</span>',
    showlegend=False,
    template="plotly_dark",
    font=dict(family="Montserrat"),
    width=1520,
    height=760,
    xaxis=dict(title_text="", showticklabels=False),
    yaxis=dict(title_text="Probability Density"),
)

# Mostrar la figura
fig2.show()

In [35]:
import plotly.express as px

fig2 = px.scatter_matrix(
    df,
    dimensions=df.columns[1:13],
    color='Power_Generated',
    title='<b style="font-size:24px;">Pairwise Relationship</b><br><span style="font-size:12px;">from Power Generated Features</span>',
    template="plotly_dark",
 )

fig2.update_layout(
    font_family="Montserrat",
    showlegend=False,
    width=1520,
    height=1520,
    yaxis_tickmode='auto',
    coloraxis_colorbar=dict(
        titleside='right',
        tickmode='array',
    ),
)

fig2.update_traces(
    hovertemplate='<b>%{xaxis.title.text}:</b> %{x}<br><b>%{yaxis.title.text}:</b> %{y}<br><b>Power Generated:</b> %{customdata}',
    customdata=df['Power_Generated'],
    diagonal_visible=False,
)

fig2.show()

In [36]:

fig3 = make_subplots(rows=1, cols=12, subplot_titles="", shared_yaxes=True)
# Iterate over subplots and add scatter plots
for i, col in enumerate(df.columns[1:13]):
    scatter = px.scatter(
        df,
        x=col,
        y='Power_Generated',
        color='Power_Generated',
    )
    
    # Update hover template
    scatter.update_traces(
        hovertemplate='<b>%{xaxis.title.text}:</b> %{x}<br><b>Power Generated:</b> %{y}',
    )
    
    # Add subplot to the figure
    fig3.add_trace(scatter['data'][0], row=1, col=i+1)
    fig3.update_xaxes(title_text=col, title_font=dict(size=10), row=1, col=i+1)

# Update layout for the overall figure
fig3.update_layout(
    font_family="Montserrat",
    showlegend=False,
    width=1520,
    height=400,
    title_text='<b style="font-size:24px;">Scatterplot between Features and Power Generated<b>',
    template="plotly_dark",
    yaxis_tickmode='auto',
    coloraxis_colorbar=dict(
        title='Power Generated',
        titleside='right',
        tickmode='array',
    ),
)

# Show the figure
fig3.show()

In [37]:
# Correlation matrices
numeric_columns = df.select_dtypes(include=[np.number]).columns.tolist()
corr_matrix  = df[numeric_columns].corr()

In [38]:
# Heatmap in plotly
#---------------------------------------------------------------------------------------------------------------------------------------------#
# Generating a discrete colorbar
from discrete_colorscale import discrete_colorscale
bvals = np.linspace(-1, 1, 21)
cmap = plt.get_cmap('inferno')
colors = cmap(np.linspace(0, 1, 20))
hex_colors = [ "#{:02x}{:02x}{:02x}".format(int(r*255), int(g*255), int(b*255)) for r, g, b, _ in colors]
dcolorsc = discrete_colorscale(bvals, hex_colors)
#---------------------------------------------------------------------------------------------------------------------------------------------#

fig4 = go.Figure(data=go.Heatmap(
        z=corr_matrix.values[::-1],
        x=corr_matrix.columns,
        y=corr_matrix.columns[::-1],
        hoverongaps=False,
        zmin=-1,
        zmax=1,
        colorscale=dcolorsc,
        colorbar=dict(title='Correlation', tickmode='array', tickvals=np.linspace(-1, 1, 21),titleside='right'),
    ))

for i in range(len(corr_matrix.columns)):
    for j in range(len(corr_matrix.columns)):
        fig4.add_annotation(
            go.layout.Annotation(
                text="{:.3f}".format(corr_matrix.iloc[i, j]),
                x=corr_matrix.columns[i],
                y=corr_matrix.columns[j],
                xref='x1',
                yref='y1',
                showarrow=False,
                font=dict(family="Montserrat", size=13, color="#262626")
            )
        )

fig4.update_layout(
    template="plotly_dark",
    width=1520,
    height=1520,
    title='<b style="font-size:24px;">Heatmap between Power Generated Features</b><br><span style="font-size:12px;">by Correlation</span>',
)

fig4.update_traces(
    hovertemplate='<extra></extra><b style="font-size:16px;"><i>ρ</i></b><b>(</b><i>%{x}</i><b>,</b> <i>%{y}</i><b>) = </b>%{z:.3f}',
        hoverlabel=dict(bgcolor="#262626")
)

fig4.show()

In [39]:
dfaux = df[numeric_columns]
dfl = dfaux[dfaux.columns[dfaux.max() <= 10]]
dfm = dfaux[dfaux.columns[(10 < dfaux.max()) & (dfaux.max() <= 400)]]
dfh = dfaux[dfaux.columns[400 < dfaux.max()]]
fig6a = px.box(
    dfl,
    x=dfl.columns,
    template="plotly_dark",
    color_discrete_sequence=["#3F7AD8"],
)

fig6a.update_traces(
    marker=dict(
        outliercolor="#3F7AD8",
        line=dict(outliercolor="#3F7AD8"),
    ),
    line=dict(color="#F2F2F2", width=0.5),
    fillcolor="#6331C5",
    hovertemplate='<extra></extra><b>%{y} = %{x:.3f}</b>',
)

fig6a.update_layout(
    xaxis_title='',
    yaxis_title=''
)

fig6b = px.box(
    dfm,
    x=dfm.columns,
    template="plotly_dark",
    color_discrete_sequence=["#3F7AD8"],
)

fig6b.update_traces(
    marker=dict(
        outliercolor="#3F7AD8",
        line=dict(outliercolor="#3F7AD8"),
    ),
    line=dict(color="#F2F2F2", width=0.5),
    fillcolor="#6331C5",
    hovertemplate='<extra></extra><b>%{y} = %{x:.3f}</b>',
)

fig6b.update_layout(
    xaxis_title='',
    yaxis_title=''
)

fig6c = px.box(
    dfh,
    x=dfh.columns,
    template="plotly_dark",
    color_discrete_sequence=["#3F7AD8"],
)

fig6c.update_traces(
    marker=dict(
        outliercolor="#3F7AD8",
        line=dict(outliercolor="#3F7AD8"),
    ),
    line=dict(color="#F2F2F2", width=0.5),
    fillcolor="#6331C5",
    hovertemplate='<extra></extra><b>%{y} = %{x:.3f}</b>',
)

fig6c.update_layout(
    xaxis_title='',
    yaxis_title=''
)

fig6 = make_subplots(
    rows=3,
    cols=1,
    horizontal_spacing=0.035,
    vertical_spacing=0.08,
)


for trace in fig6a["data"]:
    fig6.add_trace(trace, row=1, col=1)
for trace in fig6b["data"]:
    fig6.add_trace(trace, row=2, col=1)
for trace in fig6c["data"]:
    fig6.add_trace(trace, row=3, col=1)

fig6.update_layout(
    height=1520,
    width=1520,
    showlegend=False,
    title_text='<b style="font-size:20px;">Feature Values Distribution</b><br><span style="font-size:12px;">from Power Generated</span>',
    font_family="Montserrat",
    template="plotly_dark",
)

fig6.show()
del dfaux

### Data Preprocessing

In [40]:
from sklearn.preprocessing import StandardScaler
# Feature scaling
scaler = StandardScaler()
df_scaled = scaler.fit_transform(df.drop(['Timestamp'], axis=1))
df_scaled = pd.DataFrame(df_scaled, columns=df.columns[1:])

In [41]:
from sklearn.model_selection import train_test_split
X = df_scaled.drop(['Power_Generated','Wind_Direction'], axis=1)
Y = df_scaled['Power_Generated']

X_train, X_val, Y_train, Y_val = train_test_split(X, Y, test_size=0.2, random_state=27)
X.head()

Air_Temp  Relative_Humidity  Wind_Speed  Solar_Radiation     RTD_1  \
0 -0.594590           0.151437   -0.412277        -0.624963 -0.641458   
1 -0.608833           0.442055   -0.412277        -0.624112 -0.649256   
2  1.933989          -1.318476    0.201074         2.130466  2.028005   
3 -1.065160           1.443514   -0.412277        -0.625272 -0.798263   
4 -0.478415           0.164647   -0.412277        -0.624902 -0.593134   

      RTD_2     RTD_3     RTD_4     RTD_5  Array_Voltage  Array_Current  
0 -0.639425 -0.643963 -0.648326 -0.649289      -1.012638       0.554443  
1 -0.646518 -0.646877 -0.654138 -0.655367      -1.013824       0.652732  
2  2.011192  2.047851  2.025251  1.993426       1.153772      -1.507214  
3 -0.805268 -0.808305 -0.807347 -0.810596      -1.009953       1.159656  
4 -0.583778 -0.582787 -0.596837 -0.598236      -1.042489       0.355294

In [42]:
#  LSTM Model 
import tensorflow as tf
from keras.optimizers import Adam
from keras.models import Sequential
from keras.layers import LSTM, Dense

model = Sequential()
model.add(LSTM(300,activation='relu',return_sequences=True,input_shape=(11,1)))
model.add(LSTM(200,activation='relu'))
model.add(Dense(units=1, activation='linear'))
model.compile(optimizer=Adam(learning_rate=0.01), loss='mae', metrics=['mae'])

tf.random.set_seed(13)

# history = model.fit(X_train, Y_train, epochs=10, batch_size=16, validation_data=(X_val, Y_val), verbose=1)
history = model.fit(tf.expand_dims(X_train,axis=-1),Y_train, epochs=15, batch_size=16, validation_data=(tf.expand_dims(X_val, axis=-1), Y_val), verbose=1)

Epoch 1/15
50/50 [==============================] - 8s 51ms/step - loss: 0.6491 - mae: 0.6491 - val_loss: 0.3196 - val_mae: 0.3196
Epoch 2/15
50/50 [==============================] - 2s 33ms/step - loss: 0.1775 - mae: 0.1775 - val_loss: 0.1974 - val_mae: 0.1974
Epoch 3/15
50/50 [==============================] - 2s 30ms/step - loss: 0.1256 - mae: 0.1256 - val_loss: 0.2140 - val_mae: 0.2140
Epoch 4/15
50/50 [==============================] - 2s 33ms/step - loss: 0.1407 - mae: 0.1407 - val_loss: 0.1197 - val_mae: 0.1197
Epoch 5/15
50/50 [==============================] - 2s 37ms/step - loss: 0.0996 - mae: 0.0996 - val_loss: 0.1133 - val_mae: 0.1133
Epoch 6/15
50/50 [==============================] - 2s 36ms/step - loss: 0.0665 - mae: 0.0665 - val_loss: 0.0569 - val_mae: 0.0569
Epoch 7/15
50/50 [==============================] - 2s 34ms/step - loss: 0.0454 - mae: 0.0454 - val_loss: 0.0569 - val_mae: 0.0569
Epoch 8/15
50/50 [==============================] - 2s 32ms/step - loss: 0.0428 - m

In [43]:
fig7 = go.Figure()

fig7.add_trace(go.Scatter(
        y=history.history['loss'],
    mode='markers+lines',
    marker=dict(size=8, color="#6331C5"),
    line=dict(color="#6331C5"),
    hovertemplate="<extra></extra>MAE Loss: %{y}",
    name='Training Loss',
    ))

fig7.add_trace(go.Scatter(
        y=history.history['val_loss'],
    mode='markers+lines',
    marker=dict(size=8, color="#12BF80"),
    line=dict(color="#12BF80"),
    hovertemplate="<extra></extra>MAE Val. Loss: %{y}",
    name='Validation Loss',
    ))
fig7.update_layout(
    title='<b style="font-size:20px;">Comparison of Loss</b><br><span style="font-size:12px;">from Train & Validation</span>',
    xaxis_title='Epochs',
    yaxis_title='MAE',
    template="plotly_dark",
    font_family="Montserrat",
    legend=dict(x=0.8, y=1.14, bgcolor="rgba(255, 255, 255, 0.5)", orientation="h"),
    legend_font_color="#262626",
)
fig7.show()

### Testing with the rest of the dataset

In [44]:
dfr_scaled = scaler.fit_transform(df_rest.drop(['Timestamp'], axis=1))
dfr_scaled = pd.DataFrame(dfr_scaled, columns=df_rest.columns[1:])
Xr = dfr_scaled.drop(['Power_Generated','Wind_Direction'], axis=1)
Yr = dfr_scaled['Power_Generated']

model.evaluate(tf.expand_dims(Xr, axis=-1),Yr)

1/1 [==============================] - 0s 59ms/step - loss: 0.1714 - mae: 0.1714


[0.1714114099740982, 0.1714114099740982]

In [45]:
from sklearn.metrics import mean_absolute_error
y_pred = []
y_real = []
df_test = dfr_scaled.drop(['Wind_Direction'], axis=1)
feature_names = df_test.columns[:-1].tolist()
for i, row in df_test.iterrows():
    X_value = pd.DataFrame(row.iloc[:-1].values.reshape(1, -1), columns=feature_names)
    # X_value = tf.expand_dims(tf.expand_dims(row.iloc[:-1].values, axis=0), axis=-1)
    pred = model.predict(X_value)[0]        
    y_pred.append(pred)
    y_real.append(row.iloc[11])
y_pred_flat = [pred[0] for pred in y_pred]
mean_absolute_error_model = mean_absolute_error(y_real, y_pred_flat) 
print(f'Accuracy Percentage: {mean_absolute_error_model:.2f}')

1/1 [==============================] - 0s 55ms/step
Accuracy Percentage: 0.17


In [46]:
# De-scaling to plot the prediction and actual value of Power Generated
y_real_np = np.array(y_real).reshape(-1, 1)
y_pred_flat_np = np.array(y_pred_flat).reshape(-1, 1)
y_real_original_scale = scaler.inverse_transform(np.concatenate([dfr_scaled.drop(['Wind_Direction'], axis=1), y_real_np], axis=1))[:, -1]
y_pred_original_scale = scaler.inverse_transform(np.concatenate([dfr_scaled.drop(['Wind_Direction'], axis=1), y_pred_flat_np], axis=1))[:, -1]


fig8 = go.Figure()

fig8.add_trace(go.Scatter(
        y=y_real_original_scale,
    mode='markers+lines',
    marker=dict(size=8, color="#6331C5"),
    line=dict(color="#6331C5"),
    hovertemplate="<extra></extra>Real: %{y}",
    name='Real',
    ))

fig8.add_trace(go.Scatter(
        y=y_pred_original_scale,
    mode='markers+lines',
    marker=dict(size=8, color="#12BF80"),
    line=dict(color="#12BF80"),
    hovertemplate="<extra></extra>Prediction: %{y}",
    name='Prediction',
    ))
fig8.update_layout(
    title='<b style="font-size:20px;">Testing Prediction</b><br><span style="font-size:12px;">from Model</span>',
    xaxis_title='Epochs',
    yaxis_title='Power Generated',
    template="plotly_dark",
    font_family="Montserrat",
    legend=dict(x=0.8, y=1.14, bgcolor="rgba(255, 255, 255, 0.5)", orientation="h"),
    legend_font_color="#262626",
)
fig8.show()